In [1]:
import pandas as pd
from PIL import Image
import numpy as np
import torch
from tqdm import tqdm
from our_utils import MyXviewDataset
from skimage import io
from pprint import pprint
from torchmetrics.detection.mean_ap import MeanAveragePrecision
from torchvision.utils import draw_bounding_boxes
from torchvision.transforms.functional import to_pil_image
from torchvision.ops import nms
import os
pd.set_option('display.max_columns', 500)


In [15]:
dev = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
dev

device(type='cuda')

In [3]:
labelmap = {}

with open('labelmap.txt', 'r') as lbl_f:
    lines = lbl_f.readlines()
    for line in lines:
        if not line:
            continue
        c_id, c_name = line.split(':')
        labelmap[int(c_id)] = c_name.strip()
        


In [4]:
new_labels = {
    index : label for index, (key, label) in enumerate(labelmap.items())
}

In [5]:
final_df = pd.read_csv("cropped_boxes.csv")

In [6]:
import torchvision.transforms as T


def get_transform(train):
    transforms = []
    transforms.append(T.PILToTensor())
    transforms.append(T.ConvertImageDtype(torch.float))
    if train:
        transforms.append(T.ColorJitter(brightness=.5, contrast=.5, saturation=.5, hue=.1))
        transforms.append(T.Grayscale(num_output_channels=3))
        transforms.append(T.GaussianBlur(3))
        transforms.append(T.RandomAutocontrast(p=0.5))

    return T.Compose(transforms)

In [17]:
image_labels = sorted(os.listdir('./test_images/'))
test = pd.read_csv("./testDf.csv")

test = test[test["img_label"].isin(image_labels)]
testDs = MyXviewDataset(get_transform(train=False), test, os.path.abspath("./test_images/"), 60)

model = torch.load("./models/fasterRcnn.pt").to(dev)
model.eval()

FasterRCNN(
  (transform): GeneralizedRCNNTransform(
      Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
      Resize(min_size=(800,), max_size=1333, mode='bilinear')
  )
  (backbone): BackboneWithFPN(
    (body): IntermediateLayerGetter(
      (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
      (bn1): FrozenBatchNorm2d(64, eps=0.0)
      (relu): ReLU(inplace=True)
      (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
      (layer1): Sequential(
        (0): Bottleneck(
          (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn1): FrozenBatchNorm2d(64, eps=0.0)
          (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
          (bn2): FrozenBatchNorm2d(64, eps=0.0)
          (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn3): FrozenBatchNorm2d(256, eps=0.0)
          (relu): ReLU(

In [8]:
def img_show_bboxes(path, res, lab):
    
    img = io.imread(path)

    boxes = []
    labels = []

    for index, item in res.iterrows():

    
        left = item["minc"] - item["min_w"]
        up = item["minr"] - item["min_h"]
        right = item["maxc"] - item["min_w"]
        down = item["maxr"] - item["min_h"]
        
        boxes.append([left, up, right, down])
        labels.append(item['type_id'])

        
    boxes = torch.tensor(boxes)
    img = torch.tensor(img)
    img = img.permute(2,0,1)
    labels = [{"id" : x, "name": new_labels[x]} for x in labels]     
    annot_labels = ["{}-{:.2f}".format(label["name"], prob) for label, prob in zip(labels, [1 for _ in range(len(labels))])]
    output = draw_bounding_boxes(image=img,
                             boxes=boxes,
                             labels=annot_labels,
                             colors=["red" if label["name"]=="Building" else "green" for label in labels],
                             width=2
                            )  
    return to_pil_image(output)


In [9]:
def show_result_one_image(model, ds, df, imgNum, dev):
    if len(ds) <= imgNum:
        print(f"There is only {len(ds)} pictures, you tried to display {imgNum + 1}-th picture.")
        return
    
    img_lbl = ds.imgs[imgNum]
    print(img_lbl)

    tempDf = df[df['img_label'] == img_lbl]
    gt = img_show_bboxes(f"./test_images/{img_lbl}", tempDf,img_lbl)
    
    

    item = ds.__getitem__(imgNum)
    
    image = item[0][None, :].to(dev)

    res = model(image)
    indices = nms(res[0]['boxes'], res[0]['scores'], 0.7)

    nms_boxes = torch.index_select(res[0]['boxes'], 0, indices)
    nms_scores = torch.index_select(res[0]['scores'], 0, indices)
    nms_labels = torch.index_select(res[0]['labels'], 0, indices)
    
    conf = nms_scores.detach().cpu().numpy()
    conf = torch.tensor([index for index, x in enumerate(nms_scores) if x > 0.2], dtype=torch.int32).to(dev)


    nms_boxes = torch.index_select(nms_boxes, 0, conf)
    nms_scores = torch.index_select(nms_scores, 0, conf)
    nms_labels = torch.index_select(nms_labels, 0, conf)
    
    labels = [{"id" : x, "name": new_labels[x]} for x in nms_labels.detach().cpu().numpy()]
    
    imagex = 255 * item[0] # Now scale by 255
    imagex = imagex.to(torch.uint8)
    
    
    annot_labels = ["{}-{:.2f}".format(label["name"], prob) for label, prob in zip(labels, nms_scores.detach().cpu().numpy())]

    output = draw_bounding_boxes(image=imagex,
                             boxes=nms_boxes,
                             labels=annot_labels,
                             colors=["red" if label["name"]=="Building" else "green" for label in labels],
                             width=2
                            )
    output = to_pil_image(output)
    output.show(title=img_lbl)
    gt.show(title=img_lbl)
    
    

This function print the image name and shows two images. First is the prediction and second is ground truth.

In [10]:
print(len(testDs))

24


In [11]:
# number of image from the dataset loader from 0 to len(testDs)-1
imgNum = 0

In [12]:
show_result_one_image(model, testDs, final_df, imgNum, dev)

613_8_.tif


In [13]:
def label_results(model, ds, df):


    for item in tqdm(ds):
        gt = ""
        pred = ""
        imgIdx = item[1]['image_id'][0].detach().cpu().numpy()
        
        tempDf = df[df['img_label'] == ds.imgs[imgIdx]]
        
        image = item[0][None, :].to(dev)
        
        res = model(image)
        indices = nms(res[0]['boxes'], res[0]['scores'], 0.7)

        nms_boxes = torch.index_select(res[0]['boxes'], 0, indices)
        nms_scores = torch.index_select(res[0]['scores'], 0, indices)
        nms_labels = torch.index_select(res[0]['labels'], 0, indices)
        

        for box, score, label in zip(nms_boxes, nms_scores, nms_labels):
            lab = int(label.detach().cpu().numpy())
            pred += f"{new_labels[lab].replace(' ', '').replace('/','_')} {score} {int(box[0])} {int(box[1])} {int(box[2])} {int(box[3])}\n"
        
        boxes=torch.tensor([[x['minc'] - x['min_w'],x['minr'] - x['min_h'],x['maxc'] - x['min_w'],x['maxr'] - x['min_h']] for ind, x in tempDf.iterrows()])
        labels=torch.tensor([x['type_id'] for ind, x in tempDf.iterrows()])
        
        for box, label in zip(boxes, labels):
            lab = int(label.detach().cpu().numpy())
            gt += f"{new_labels[lab].replace(' ', '').replace('/','_')} {box[0]} {box[1]} {box[2]} {box[3]}\n"

        with open(f"./mAP/ground-truth/{ds.imgs[imgIdx].split('.')[0]}.txt", "w") as f:
            f.write(gt)
        with open(f"./mAP/detection-results/{ds.imgs[imgIdx].split('.')[0]}.txt", "w") as f:
            f.write(pred)



In [18]:
label_results(model, testDs, final_df)

100%|██████████████████████████████████████████████████████████████████████████████████| 24/24 [00:06<00:00,  3.91it/s]


The mAP score was then calculated by code from github that is mentioned in final 